In [37]:
import numpy as np
import matplotlib.pyplot as plt
from numpy import sqrt 
from operator import itemgetter

In [38]:
#utils
def Sqr(a):
    return a*a
 
def Distance(x1,y1,x2,y2):
    return sqrt(Sqr(y2-y1)+Sqr(x2-x1))

In [39]:
fileToOpen = "p01.txt"

m = 0
n = 0
t = 0

In [40]:
ct = 0
with open(fileToOpen) as fin:
    rows = (line.split() for line in fin)
    for row in rows:
        if ct == 0:
            m = int(row[0])
            n = int(row[1])
            t = int(row[2])
            tmp = np.zeros([int(t),2])
            depotz = np.zeros([t, 5])
            customerz = np.zeros([n,5])
        elif ct > 0 and ct <= t:
            for depot in tmp:
                tmp[ct-1] = (row[0],row[1])
        elif ct >= t+1 and ct <= n+t:
            for element in range(n):
                a = n+t+1
                customerz[ct-a] = (row[0],row[1],row[2],row[3],row[4])
        elif ct > t+n:
            a = n+t+1
            for element in range(t):
                mdr = tmp[element][0]
                mlv = tmp[element][1]
                depotz[ct-a] = (row[0],row[1],row[2],mdr,mlv)
        ct = ct + 1
                
print (str(m) +" "+ str(n) +" "+ str(t) )

vehiclesMxW = depotz[0][4]
nbVehicles = 16 #np.random.randint(t, m*t)  #aka number of routes
indivPerGen = 100

4 50 4


In [41]:

print(depotz)
print(customerz)

ml = depotz[0][4]

[[51. 20. 20.  0. 80.]
 [52. 30. 40.  0. 80.]
 [53. 50. 30.  0. 80.]
 [54. 60. 50.  0. 80.]]
[[ 1. 37. 52.  0.  7.]
 [ 2. 49. 49.  0. 30.]
 [ 3. 52. 64.  0. 16.]
 [ 4. 20. 26.  0.  9.]
 [ 5. 40. 30.  0. 21.]
 [ 6. 21. 47.  0. 15.]
 [ 7. 17. 63.  0. 19.]
 [ 8. 31. 62.  0. 23.]
 [ 9. 52. 33.  0. 11.]
 [10. 51. 21.  0.  5.]
 [11. 42. 41.  0. 19.]
 [12. 31. 32.  0. 29.]
 [13.  5. 25.  0. 23.]
 [14. 12. 42.  0. 21.]
 [15. 36. 16.  0. 10.]
 [16. 52. 41.  0. 15.]
 [17. 27. 23.  0.  3.]
 [18. 17. 33.  0. 41.]
 [19. 13. 13.  0.  9.]
 [20. 57. 58.  0. 28.]
 [21. 62. 42.  0.  8.]
 [22. 42. 57.  0.  8.]
 [23. 16. 57.  0. 16.]
 [24.  8. 52.  0. 10.]
 [25.  7. 38.  0. 28.]
 [26. 27. 68.  0.  7.]
 [27. 30. 48.  0. 15.]
 [28. 43. 67.  0. 14.]
 [29. 58. 48.  0.  6.]
 [30. 58. 27.  0. 19.]
 [31. 37. 69.  0. 11.]
 [32. 38. 46.  0. 12.]
 [33. 46. 10.  0. 23.]
 [34. 61. 33.  0. 26.]
 [35. 62. 63.  0. 17.]
 [36. 63. 69.  0.  6.]
 [37. 32. 22.  0.  9.]
 [38. 45. 35.  0. 15.]
 [39. 59. 15.  0. 14.]
 [40.  5. 

In [42]:
#np.random.seed(0)

In [43]:
class Customer:
    def __init__(self,id,x,y,duration,demand):
        self.id = id
        self.x = x
        self.y = y 
        self.duration = duration
        self.demand = demand
        
            
    def __repr__(self):
        return "Client: " +str(int(self.id)) +" "+ str(int(self.x)) +" "+ str(int(self.y)) + " " + str(int(self.duration)) + " " + str(int(self.demand))

In [44]:
#Is a set of chromosomes
class Route:
    def __init__(self, ID, depot):
        self.id = ID
        self.depot = depot #depot assigned to this route
        self.customers = list() 
        self.capacity = 0 #total of the demand
        self.ttlDistance = 0 #Ttl distance of the road
        self.maxLoad = ml #maxLoad per vehicles
        self.oc = 0
        
    def getTotalDistanceR(self):
        ttl = 0
        vTotal = 0
        if len(self.customers) == 0:
            return 0
        first_cust = self.customers[0]
        last_cust = self.customers[-1]
        #calculating cost between each cust
        for c in range(len(self.customers)-1):
            #print("x: " +str(self.customers[c].x) +" y: " + str(self.customers[c].y))
            ttl = ttl + Distance(self.customers[c].x,self.customers[c].y,self.customers[c+1].x,self.customers[c+1].y)
        #and between depot at the begining and end of the route since the veh needs to stop where it started
        addtt = 0
        addtt = addtt + Distance(first_cust.x, first_cust.y, self.depot.x, self.depot.y)
        addtt = addtt + Distance(last_cust.x, last_cust.y, self.depot.x, self.depot.y)
        vTotal = ttl + addtt
                #print("Distance bw cust: " + str(ttl) + " Added to beg and end: " + str(addtt)+ " Total: " + str(vTotal))
        self.ttlDistance = vTotal
        #print('ttR'+ str( self.ttlDistance))
        return vTotal
    
    def getCapacity(self):
        return self.capacity
    
    #Check if the capacity is greater than allowed (reassign self too)
    def isOverloaded(self):
        ttl = 0
        for c in self.customers:
            ttl = ttl + c.demand
        self.capacity = ttl
        if ttl > self.maxLoad:
            self.oc = self.oc + 1
            return True
        else:
            return False
        
    def __repr__(self):
        return "Route: " +str(self.id) +" "+ str(self.depot) + " " + str(len(self.customers))+ " Sz:"+ str(len(self.customers)) + " C:" + str(self.capacity) + " T:" + str(self.ttlDistance)

In [45]:
#Is a set of genes
class Depot:
    def __init__(self, id, x, y): 
        self.id = id
        self.x = x
        self.y = y
        self.customers = list()
        self.maxVehicle = m
        self.routes = list()
        for nbR in range(self.maxVehicle):
            self.routes.append(Route(nbR, self))
        
    #assign a customer to a random route    
    def addCustomer(self,c):
        #Selecting which route to assign it to
        choice = np.random.randint(0,self.maxVehicle)
        #print( str(self.id)+ ": putting in:" + str(choice) + " " +str(c))
        self.routes[choice].customers.append(c)
    
    def getCapacity(self):
        ttlC = 0
        l = list()
        ro = list()
        for r in self.routes:
            ttlC = ttlC + r.capacity
            l.append(r.capacity)
            ro.append(r.oc)
        return ttlC, l, ro
    
    def getTotalDistanceD(self):
        distTotale = 0
        for r in self.routes:
            #we make the distance twice as great to avoid overloading
            if r.isOverloaded():
                distTotale = distTotale +r.getTotalDistanceR()*5
                #print("-" + str(distTotale))
            else:
                distTotale = distTotale +r.getTotalDistanceR()
                #print("+" + str(distTotale))
            
        """print(distTotale)
        print()"""
        return distTotale
    
    def __repr__(self):
        return "Depot: " + str(self.id) +" "  + str(self.x) +" "+ str(self.y) + " "+ str(len(self.routes) )

In [46]:
#Is a set od Depots representing a solution
class Individual:
    def __init__(self, id , gen):
        self.id = id
        self.gen = gen
        self.fitness = 9999
        self.depots = list()
        self.proba = 0 #chances for it to be picked as a parent
        
    def calculFitness(self):
        distTotale = 0
        for dpt in self.depots:
            distTotale = distTotale + dpt.getTotalDistanceD()
        self.fitness = distTotale

    def getTtlCapacity(self):
        ttlC = 0
        l = list()
        ovc = list()
        for d in self.depots:
            ttlC = ttlC + d.getCapacity()[0]
            l.append( d.getCapacity()[0])
        #overCapacity
        for oc in d.getCapacity()[2]:
            ovc.append(oc)
        return ttlC, l, ovc
        
    def addDepot(self,id, x, y):
        self.depots.append(Depot(id, x, y))
    
    
    def __repr__(self):
        return "Indiv:{}/{} {} {}".format(self.id, self.gen, str(int(self.fitness)), str(len(self.depots)))

In [47]:
def makeSolutionInit(i):
    #Making the t depots in the indiv
    for dpt in depotz:
        i.addDepot(dpt[0], dpt[1], dpt[2])
    #for each customer, assign them to the best depot
    for cli in customerz:
        bestDist = 99999
        closestDepot = None
        for testedDepot in i.depots:
            distToDepot = Distance(testedDepot.x, testedDepot.y, cli[1], cli[2])
            if distToDepot < bestDist:
                bestDist = distToDepot
                closestDepot = testedDepot
        closestDepot.addCustomer(Customer(cli[0], cli[1], cli[2], cli[3], cli[4]))
    return i

In [48]:
def makeGen0(individuals, ipg, epoch):
    while len(individuals) < ipg:
        i = Individual(len(individuals),epoch)
        i = makeSolutionInit(i)
        individuals.append(i)
        i.calculFitness()
    print(individuals)
    return individuals

In [49]:
#Given arr, an array , and index, a float this function return the right element from the assosiative array (used after normalization to chose a parent)
def probaPick(arr, index):
    #print(index)
    """print(index)"""
    if index < arr[0][0]: #checks if index given is small enough to be first value (avoid looping)
            return arr[0][1]
    if index > arr[len(arr)-1][0]: #Checks the last value (avoid loop)
        return arr[len(arr)-1][1]
    for el in range(len(arr)):
        #print(arr[el][0])
        if arr[el][0] <= index and arr[el+1][0] >= index:
            return arr[el][1] 

In [50]:
#next few lines are inspired by this : https://stackoverflow.com/questions/2772882/picking-a-random-item-based-on-probabilities
#normalized probability to have a greater chance to select the fitest candidate as a parent
def chooseParents(individuals):
    print("Selecting parents ...")
    listVal = list()
    size = 0
    for indi in individuals:
        size = size + 1
        listVal.append((indi.fitness, indi))
    """print(listVal)
    print()"""
    #sort array by value not indi
    listVal.sort(key=itemgetter(0), reverse=True)
    #assign probability depending of where in the list
    ct = 1
    for el in range(len(listVal)):
        indi = listVal[el][1]
        listVal[el] = [ct, indi]
        ct = ct + 1
    """print(listVal)
    print()"""
    #calculate cumulative proba
    lastList = list()
    cumul = 1
    for el in range(len(listVal)):
        if el == 0:
            listVal[el][0] = 1
        else:
            indi = listVal[el][1]
            cumul = listVal[el][0] + cumul
            listVal[el] = (cumul, indi)
    #normalize the probabilities
    """print(listVal)"""
    for el in range(len(listVal)):
        listVal[el] = (listVal[el][0]/cumul*100,listVal[el][1])
    """print(listVal)"""
    #chose the two parents    
    choice = np.random.uniform(0,100)
    parent1 = probaPick(listVal, choice)
    choice = np.random.uniform(0,100)
    parent2 = probaPick(listVal, choice)
    #Must make sure to not have the same parents
    while parent1.id ==parent2.id: #keep changing parent2 until it's not the sampe as parent1
        print("Same parent rerolling ... parent2")
        choice = np.random.uniform(0,100)
        parent2= probaPick(listVal, choice)
    
    return parent1, parent2

In [51]:
# Recombines two individuals (parents) to produce two new individuals (offspring),
# by applying Best Cost Route Crossover:
# 1. Randomly select depot to undergo reproduction
# 2. Randomly select a route from each parent
# 3. For each selected route, remove all customers in that route from the other parent
# 4. For each customer c that was removed from parent p, insert customer c back in parent p at best location.
def crossover(parent1, parent2):
    
    choiceDepot = np.random.randint(0,t)
    depot1 = parent1.depots[choiceDepot]
    choiceRoute = np.random.randint(0,m)
    route1 = depot1.routes[choiceRoute]
    
    choiceDepot = np.random.randint(0,t)
    choiceRoute = np.random.randint(0,m)
    depot2 = parent2.depots[choiceDepot]
    route2 = depot2.routes[choiceRoute]
    
    removedCust1 = list()
    removedCust2 = list()
    
    #Check if the customer is in the other parent
    print(route1.customers)
    print(route2.customers)
    for c1 in route1.customers:
        for c2 in route2.customers:
            if c1.id == c2.id:
                print(len(route2.customers))
                print(c2.id)
                removedCust2.append(c2)
                route2.customers.remove(c2)
                for cc in route2.customers:
                    print(cc.id)
        print("r2c" + str(len(route2.customers)))
    
    for cust in removedCust2:
        bestCost = 99999
        bestPlace = 0
        for i in range(len(route2.customers)):
            #print("it: " + str(i) )
            if(len(route2.customers) == 0): 
                cost = (Distance(cust.x, cust.y, depot2.x, depot2.y))*2
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            if(len(route2.customers) == 1):
                cost = Distance(cust.x, cust.y, depot2.x, depot2.y) + Distance(cust.x, cust.y, route2.customers[0].x, route2.customers[0].y)
                cost = cost - Distance(depot2.x, depot2.y,  route2.customers[0].x, route2.customers[0].y)
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            if i == 0 :
                if len(route2.customers) > 1:
                    cost = (Distance(cust.x, cust.y, depot2.x, depot2.y)) + Distance(cust.x, cust.y, route2.customers[1].x, route2.customers[1].y) - Distance(depot2.x, depot2.y, route2.customers[1].x, route2.customers[1].y) 
                    if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
                        
            elif i == len(route2.customers)-1:
                cost = (Distance(cust.x, cust.y, depot2.x, depot2.y)) + Distance(cust.x, cust.y, route2.customers[len(route2.customers)-1].x, route2.customers[len(route2.customers)-1].y) - Distance(depot2.x, depot2.y, route2.customers[len(route2.customers)-1].x, route2.customers[len(route2.customers)-1].y) 
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
                        
            else: #cost = d from cust to both cust - dist(ac1, ac2)
                cost = (Distance(cust.x, cust.y,  route2.customers[i].x,  route2.customers[i].y))+ (Distance(cust.x, cust.y,  route2.customers[i+1].x,  route2.customers[i+1].y)) 
                cost = cost - (Distance(route2.customers[i].x,  route2.customers[i].y,  route2.customers[i+1].x,  route2.customers[i+1].y))
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            print("Cost at {}: {}/{} bp:{}".format(i, cost, bestCost, bestPlace))
        route2.customers.insert(bestPlace, cust)
        #print("r2b" + str(len(route2.customers)))
                        
                
    """#get best place to put customer back
    for cust in removedCust2:
        bestCost = 99999
        bestPlace = 0
        #For each deleted customer
        for i in range(len(route2.customers)):
            #If creating new route cost = d(c, depot)*2
            if len(route2.customers) == 0:
                cost = (Distance(cust.x, cust.y, depot2.x, depot2.y))*2
            #If at the begining or end of the list, cost = d(depot, c) + d(c, c(n-+1)) - d(c(n-+1), depot)
            print("it: " + str(i) )
            if i == 0 :
                if len(route2.customers) == 1:
                    cost = (Distance(cust.x, cust.y, depot2.x, depot2.y)) + Distance(cust.x, cust.y, route2.customers[1].x, route2.customers[1].y) - Distance(depot2.x, depot2.y, route2.customers[1].x, route2.customers[1].y) 
                    if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            elif i == len(route2.customers)-1:
                cost = (Distance(cust.x, cust.y, depot2.x, depot2.y)) + Distance(cust.x, cust.y, route2.customers[len(route2.customers)-1].x, route2.customers[len(route2.customers)-1].y) - Distance(depot2.x, depot2.y, route2.customers[len(route2.customers)-1].x, route2.customers[len(route2.customers)-1].y) 
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            else: #cost = d from cust to both cust - dist(ac1, ac2)
                cost = (Distance(cust.x, cust.y,  route2.customers[i].x,  route2.customers[i].y))+ (Distance(cust.x, cust.y,  route2.customers[i+1].x,  route2.customers[i+1].y)) 
                cost = cost - (Distance(route2.customers[i].x,  route2.customers[i].y,  route2.customers[i+1].x,  route2.customers[i+1].y))
                if cost < bestCost :
                        bestCost = cost
                        bestPlace = i
            print("Cost at {}: {}/{} bp:{}".format(i, cost, bestCost, bestPlace))
        route2.customers.insert(bestPlace, cust)
        print("r2b" + str(len(route2.customers)))"""
    return parent2
                
    
    """
    print(len(route1.customers))
    for c in route1.customers:
        removedCust1.append(c)
    route1.customers.clear()
    print(len(route2.customers))
    for c in route2.customers:
        removedCust2.append(c)
    route2.customers.clear()"""

    """print(choiceDepot)
    print(choiceRoute)"""
    print(route1)
    print(route2)
    print(removedCust1)
    print(removedCust2)

In [52]:
def mutate(child):
    choice = np.random.randint(0,2)
    choiceDepot = np.random.randint(0,t)
    depot1 = child.depots[choiceDepot]
    choiceRoute = np.random.randint(0,m)
    route1 = depot1.routes[choiceRoute]
    cust = None
    if len(route1.customers) >= 1:
        choiceCust = np.random.randint(0, len(route1.customers))
        cust = route1.customers[choiceCust]
        route1.customers.remove(cust)
    else:
        if len(route1.customers)==1:
            cust = route1.customers[0]
            route1.customers.remove(cust)
        else: 
            return child
    choiceDepot2 = np.random.randint(0,t)
    depot2 = child.depots[choiceDepot2]
    choiceRoute2 = np.random.randint(0,m)
    route2 = depot2.routes[choiceRoute2]
    route2.customers.append(cust)
    print("Mutated : {} from {} {} to {} {}".format(child, depot1, route1, depot2, route2)) 
    print(child)
    return child

In [53]:
def mainProg(epochs=50, indivPerGen=200, chanceMutation=100):  
    individuals = list()
    individualsNextGen = list()
    #Epoch is a generation
    for epoch in range(epochs):
        print("Generation: " + str(epoch))
        if epoch == 0:
            individualsNextGen = makeGen0(individuals, indivPerGen, epoch)
        else:
            #Main loop
            #We need to select 2 parents (depending of their fitness)
            print(individuals)
            
            while(len(individualsNextGen) < indivPerGen ):
                parent1 , parent2 = chooseParents(individuals)
                print(parent1)
                print(parent2)
                #Cross their genes
                child1 = crossover(parent1, parent2)
                child2 = crossover(parent2, parent1)

                print(child1)
                print(child2)

                individualsNextGen.append(child1)
                individualsNextGen.append(child2)
                
                if np.random.randint(0,100) < chanceMutation:
                    child1 = mutate(child1)
                if np.random.randint(0,100) < chanceMutation:
                    child2 = mutate(child2)
                
                
            #Give a chance to mutate          
            
        print("--------------")
        individuals = individualsNextGen.copy()
        individualsNextGen.clear()
        
        
                
                
        """ttl = 0
        for i in individuals:
            for d in i.depots:
                #print(d)
                print(d)
                for r in d.routes:
                    #ttl = ttl + len(r.customers)
                    print((r.id))
                    print(r.oc)
                    print(r.capacity)
            print("Indiv" + str(i))
        print(ttl)"""

In [ ]:
individuals = list()
individualsNextGen = list()
mainProg()

Generation: 0
[Indiv:0/0 1470 4, Indiv:1/0 3142 4, Indiv:2/0 2096 4, Indiv:3/0 1855 4, Indiv:4/0 2094 4, Indiv:5/0 2878 4, Indiv:6/0 2500 4, Indiv:7/0 1773 4, Indiv:8/0 1428 4, Indiv:9/0 2343 4, Indiv:10/0 1873 4, Indiv:11/0 1864 4, Indiv:12/0 3145 4, Indiv:13/0 1520 4, Indiv:14/0 1931 4, Indiv:15/0 2653 4, Indiv:16/0 2557 4, Indiv:17/0 2863 4, Indiv:18/0 2700 4, Indiv:19/0 2021 4, Indiv:20/0 1917 4, Indiv:21/0 2886 4, Indiv:22/0 1939 4, Indiv:23/0 2631 4, Indiv:24/0 1739 4, Indiv:25/0 2219 4, Indiv:26/0 2299 4, Indiv:27/0 1889 4, Indiv:28/0 1392 4, Indiv:29/0 2189 4, Indiv:30/0 1874 4, Indiv:31/0 2734 4, Indiv:32/0 2175 4, Indiv:33/0 2860 4, Indiv:34/0 2043 4, Indiv:35/0 3215 4, Indiv:36/0 2299 4, Indiv:37/0 3420 4, Indiv:38/0 2265 4, Indiv:39/0 2270 4, Indiv:40/0 1594 4, Indiv:41/0 2346 4, Indiv:42/0 1895 4, Indiv:43/0 1951 4, Indiv:44/0 1755 4, Indiv:45/0 2431 4, Indiv:46/0 2033 4, Indiv:47/0 2087 4, Indiv:48/0 2048 4, Indiv:49/0 2309 4, Indiv:50/0 2084 4, Indiv:51/0 2127 4, Indiv:5

[Client: 1 37 52 0 7, Client: 12 31 32 0 29, Client: 24 8 52 0 10]
[Client: 5 40 30 0 21, Client: 10 51 21 0 5]
r2c2
r2c2
r2c2
[Client: 2 49 49 0 30, Client: 22 42 57 0 8, Client: 29 58 48 0 6]
[Client: 5 40 30 0 21, Client: 30 58 27 0 19, Client: 34 61 33 0 26, Client: 38 45 35 0 15, Client: 39 59 15 0 14]
r2c5
r2c5
r2c5
Indiv:112/0 2881 4
Indiv:107/0 2194 4
Mutated : Indiv:112/0 2881 4 from Depot: 54.0 60.0 50.0 4 Route: 2 Depot: 54.0 60.0 50.0 4 1 Sz:1 C:33.0 T:39.3273375556839 to Depot: 52.0 30.0 40.0 4 Route: 1 Depot: 52.0 30.0 40.0 4 7 Sz:7 C:109.0 T:144.80120994206823
Indiv:112/0 2881 4
Mutated : Indiv:107/0 2194 4 from Depot: 51.0 20.0 20.0 4 Route: 0 Depot: 51.0 20.0 20.0 4 3 Sz:3 C:25.0 T:37.983469790261154 to Depot: 51.0 20.0 20.0 4 Route: 0 Depot: 51.0 20.0 20.0 4 3 Sz:3 C:25.0 T:37.983469790261154
Indiv:107/0 2194 4
Selecting parents ...
Indiv:177/0 2575 4
Indiv:63/0 1884 4
[Client: 3 52 64 0 16, Client: 21 62 42 0 8, Client: 28 43 67 0 14, Client: 29 58 48 0 6, Client: 35

Indiv:90/0 1751 4
Indiv:146/0 1707 4
Mutated : Indiv:90/0 1751 4 from Depot: 51.0 20.0 20.0 4 Route: 0 Depot: 51.0 20.0 20.0 4 2 Sz:2 C:22.0 T:48.07814716249038 to Depot: 54.0 60.0 50.0 4 Route: 1 Depot: 54.0 60.0 50.0 4 5 Sz:5 C:49.0 T:99.32416689957326
Indiv:90/0 1751 4
Mutated : Indiv:146/0 1707 4 from Depot: 51.0 20.0 20.0 4 Route: 0 Depot: 51.0 20.0 20.0 4 2 Sz:2 C:64.0 T:67.26292514548352 to Depot: 52.0 30.0 40.0 4 Route: 0 Depot: 52.0 30.0 40.0 4 5 Sz:5 C:80.0 T:148.5349096505204
Indiv:146/0 1707 4
Selecting parents ...
Indiv:142/0 2098 4
Indiv:124/0 1974 4
[Client: 10 51 21 0 5, Client: 33 46 10 0 23, Client: 38 45 35 0 15, Client: 39 59 15 0 14]
[Client: 20 57 58 0 28, Client: 29 58 48 0 6]
r2c2
r2c2
r2c2
r2c2
[Client: 2 49 49 0 30, Client: 21 62 42 0 8, Client: 28 43 67 0 14, Client: 36 63 69 0 6]
[Client: 5 40 30 0 21, Client: 16 52 41 0 15, Client: 34 61 33 0 26, Client: 49 48 28 0 18, Client: 50 56 37 0 10]
r2c5
r2c5
r2c5
r2c5
Indiv:124/0 1974 4
Indiv:142/0 2098 4
Mutated 

Selecting parents ...
Indiv:100/0 2008 4
Indiv:77/0 1780 4
[Client: 39 59 15 0 14, Client: 50 56 37 0 10]
[Client: 21 62 42 0 8]
r2c1
r2c1
[Client: 1 37 52 0 7, Client: 14 12 42 0 21, Client: 43 5 64 0 11, Client: 46 32 39 0 5]
[Client: 33 46 10 0 23]
r2c1
r2c1
r2c1
r2c1
Indiv:77/0 1780 4
Indiv:100/0 2008 4
Mutated : Indiv:77/0 1780 4 from Depot: 54.0 60.0 50.0 4 Route: 1 Depot: 54.0 60.0 50.0 4 2 Sz:2 C:46.0 T:42.46693505456271 to Depot: 54.0 60.0 50.0 4 Route: 1 Depot: 54.0 60.0 50.0 4 2 Sz:2 C:46.0 T:42.46693505456271
Indiv:77/0 1780 4
Mutated : Indiv:100/0 2008 4 from Depot: 53.0 50.0 30.0 4 Route: 2 Depot: 53.0 50.0 30.0 4 1 Sz:1 C:24.0 T:48.916003453003306 to Depot: 51.0 20.0 20.0 4 Route: 3 Depot: 51.0 20.0 20.0 4 2 Sz:2 C:7.0 T:41.036569057366385
Indiv:100/0 2008 4
Selecting parents ...
Indiv:63/0 1884 4
Indiv:24/0 1739 4
[Client: 1 37 52 0 7, Client: 14 12 42 0 21, Client: 32 38 46 0 12, Client: 48 25 55 0 17]
[Client: 5 40 30 0 21, Client: 9 52 33 0 11, Client: 33 46 10 0 23,

r2c3
r2c3
r2c3
r2c3
r2c3
r2c3
Indiv:166/0 1681 4
Indiv:184/0 1516 4
Mutated : Indiv:166/0 1681 4 from Depot: 52.0 30.0 40.0 4 Route: 0 Depot: 52.0 30.0 40.0 4 3 Sz:3 C:48.0 T:75.27413804142721 to Depot: 51.0 20.0 20.0 4 Route: 0 Depot: 51.0 20.0 20.0 4 4 Sz:4 C:19.0 T:41.36038476658385
Indiv:166/0 1681 4
Mutated : Indiv:184/0 1516 4 from Depot: 53.0 50.0 30.0 4 Route: 1 Depot: 53.0 50.0 30.0 4 2 Sz:2 C:55.0 T:69.43223666359178 to Depot: 53.0 50.0 30.0 4 Route: 2 Depot: 53.0 50.0 30.0 4 5 Sz:5 C:73.0 T:54.388669553694605
Indiv:184/0 1516 4
Selecting parents ...
Indiv:28/0 1392 4
Indiv:13/0 1520 4
[Client: 8 31 62 0 23, Client: 32 38 46 0 12, Client: 43 5 64 0 11, Client: 46 32 39 0 5, Client: 47 25 32 0 25]
[Client: 3 52 64 0 16, Client: 28 43 67 0 14, Client: 35 62 63 0 17, Client: 36 63 69 0 6]
r2c4
r2c4
r2c4
r2c4
r2c4
[Client: 3 52 64 0 16, Client: 28 43 67 0 14, Client: 35 62 63 0 17, Client: 36 63 69 0 6]
[]
r2c0
r2c0
r2c0
r2c0
Indiv:13/0 1520 4
Indiv:28/0 1392 4
Mutated : Indiv:13

...

Selecting parents ...
Indiv:103/0 1042 4
Indiv:69/0 1026 4
[Client: 2 49 49 0 30, Client: 26 27 68 0 7, Client: 35 62 63 0 17, Client: 1 37 52 0 7, Client: 16 52 41 0 15, Client: 50 56 37 0 10, Client: 8 31 62 0 23, Client: 6 21 47 0 15, Client: 13 5 25 0 23, Client: 32 38 46 0 12, Client: 49 48 28 0 18, Client: 12 31 32 0 29, Client: 41 10 17 0 27]
[Client: 37 32 22 0 9, Client: 47 25 32 0 25]
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
r2c2
[Client: 38 45 35 0 15]
[Client: 3 52 64 0 16, Client: 30 58 27 0 19, Client: 24 8 52 0 10, Client: 10 51 21 0 5, Client: 29 58 48 0 6, Client: 14 12 42 0 21, Client: 33 46 10 0 23]
r2c7
Indiv:69/0 1026 4
Indiv:103/0 1042 4
Mutated : Indiv:69/0 1026 4 from Depot: 54.0 60.0 50.0 4 Route: 1 Depot: 54.0 60.0 50.0 4 1 Sz:1 C:28.0 T:17.08800749063506 to Depot: 53.0 50.0 30.0 4 Route: 0 Depot: 53.0 50.0 30.0 4 3 Sz:3 C:70.0 T:70.8657934836277
Indiv:69/0 1026 4
Selecting parents ...
Same parent rerolling ... parent2
Same parent rerolling 

[Client: 2 49 49 0 30, Client: 35 62 63 0 17, Client: 26 27 68 0 7, Client: 1 37 52 0 7, Client: 16 52 41 0 15, Client: 50 56 37 0 10, Client: 8 31 62 0 23, Client: 6 21 47 0 15, Client: 41 10 17 0 27, Client: 42 21 10 0 13, Client: 13 5 25 0 23, Client: 49 48 28 0 18, Client: 12 31 32 0 29, Client: 23 16 57 0 16]
Indiv:69/0 1026 4
Indiv:103/0 1042 4
Mutated : Indiv:69/0 1026 4 from Depot: 54.0 60.0 50.0 4 Route: 2 Depot: 54.0 60.0 50.0 4 0 Sz:0 C:8.0 T:16.492422502470642 to Depot: 52.0 30.0 40.0 4 Route: 0 Depot: 52.0 30.0 40.0 4 3 Sz:3 C:79.0 T:112.7254916869424
Indiv:69/0 1026 4
Mutated : Indiv:103/0 1042 4 from Depot: 54.0 60.0 50.0 4 Route: 1 Depot: 54.0 60.0 50.0 4 0 Sz:0 C:42.0 T:49.228951282753385 to Depot: 51.0 20.0 20.0 4 Route: 3 Depot: 51.0 20.0 20.0 4 3 Sz:3 C:70.0 T:75.72805273534027
Indiv:103/0 1042 4
Selecting parents ...
Same parent rerolling ... parent2
Same parent rerolling ... parent2
Indiv:69/0 1026 4
Indiv:103/0 1042 4
[Client: 6 21 47 0 15, Client: 3 52 64 0 16, 

47.0
49.0
45.0
r2c8
Cost at 0: 3.0773392975124096/3.0773392975124096 bp:0
Cost at 1: 2.8669539526399674/2.8669539526399674 bp:1
Cost at 2: 0.30453770512494316/0.30453770512494316 bp:2
Cost at 3: 20.396078054371138/0.30453770512494316 bp:2
Cost at 4: 5.986130748425456/0.30453770512494316 bp:2
Cost at 5: 16.11765962465621/0.30453770512494316 bp:2
Cost at 6: 43.10368606439616/0.30453770512494316 bp:2
Cost at 7: 32.88874502016059/0.30453770512494316 bp:2
[]
[Client: 29 58 48 0 6]
Indiv:69/0 1026 4
Indiv:103/0 1042 4
Mutated : Indiv:69/0 1026 4 from Depot: 54.0 60.0 50.0 4 Route: 3 Depot: 54.0 60.0 50.0 4 2 Sz:2 C:67.0 T:82.90358498624387 to Depot: 52.0 30.0 40.0 4 Route: 3 Depot: 52.0 30.0 40.0 4 7 Sz:7 C:79.0 T:90.26506411218608
Indiv:69/0 1026 4
Selecting parents ...
Indiv:103/0 1042 4
Indiv:69/0 1026 4
[Client: 24 8 52 0 10, Client: 40 5 6 0 7, Client: 32 38 46 0 12, Client: 9 52 33 0 11, Client: 48 25 55 0 17]
[Client: 34 61 33 0 26]
r2c1
r2c1
r2c1
r2c1
r2c1
[Client: 5 40 30 0 21]
[Cli

Indiv:103/0 1042 4
Indiv:69/0 1026 4
Mutated : Indiv:103/0 1042 4 from Depot: 51.0 20.0 20.0 4 Route: 2 Depot: 51.0 20.0 20.0 4 1 Sz:1 C:7.0 T:41.036569057366385 to Depot: 54.0 60.0 50.0 4 Route: 3 Depot: 54.0 60.0 50.0 4 3 Sz:3 C:0 T:0
Indiv:103/0 1042 4
Mutated : Indiv:69/0 1026 4 from Depot: 53.0 50.0 30.0 4 Route: 1 Depot: 53.0 50.0 30.0 4 9 Sz:9 C:23.0 T:40.792156108742276 to Depot: 52.0 30.0 40.0 4 Route: 2 Depot: 52.0 30.0 40.0 4 4 Sz:4 C:37.0 T:84.25128305005276
Indiv:69/0 1026 4
Selecting parents ...
Indiv:69/0 1026 4
Indiv:103/0 1042 4
[]
[Client: 20 57 58 0 28, Client: 7 17 63 0 19, Client: 21 62 42 0 8]
[Client: 16 52 41 0 15]
[Client: 30 58 27 0 19, Client: 26 27 68 0 7]
r2c2
Indiv:103/0 1042 4
Indiv:69/0 1026 4
Mutated : Indiv:103/0 1042 4 from Depot: 52.0 30.0 40.0 4 Route: 0 Depot: 52.0 30.0 40.0 4 0 Sz:0 C:47.0 T:79.41874801237687 to Depot: 52.0 30.0 40.0 4 Route: 3 Depot: 52.0 30.0 40.0 4 2 Sz:2 C:76.0 T:108.90747446853753
Indiv:103/0 1042 4
Mutated : Indiv:69/0 1026 

Indiv:69/0 1026 4
Indiv:103/0 1042 4
[Client: 46 32 39 0 5]
[Client: 49 48 28 0 18, Client: 2 49 49 0 30, Client: 35 62 63 0 17, Client: 1 37 52 0 7, Client: 41 10 17 0 27, Client: 50 56 37 0 10, Client: 13 5 25 0 23, Client: 8 31 62 0 23, Client: 12 31 32 0 29, Client: 23 16 57 0 16, Client: 37 32 22 0 9, Client: 44 30 15 0 16, Client: 42 21 10 0 13, Client: 46 32 39 0 5, Client: 27 30 48 0 15]
15
46.0
49.0
2.0
35.0
1.0
41.0
50.0
13.0
8.0
12.0
23.0
37.0
44.0
42.0
27.0
r2c14
Cost at 0: 1.1830946687405017/1.1830946687405017 bp:0
Cost at 1: 39.03685517337031/1.1830946687405017 bp:0
Cost at 2: 25.034133134285884/1.1830946687405017 bp:0
Cost at 3: 0.8370144387915275/0.8370144387915275 bp:3
Cost at 4: 5.036142713854872/0.8370144387915275 bp:3
Cost at 5: 2.104254219356747/0.8370144387915275 bp:3
Cost at 6: 8.213865299553717/0.8370144387915275 bp:3
Cost at 7: 0.09279667830815086/0.09279667830815086 bp:7
Cost at 8: 1.9994974952235651/0.09279667830815086 bp:7
Cost at 9: 2.5994263477968786/0.092

In [1449]:
a = Customer(1,10,10,0,0)
a1 = Customer(1,10,10,0,0)
a2 = Customer(1,10,10,0,0)
al = list([a,a1,a2])
al.remove(a2)
print(a in al)
print(al)

True
[Client: 1 10 10 0 0, Client: 1 10 10 0 0]
